In [ ]:
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
import json
import numpy as np
import scipy as sp
import pandas as pd
import scipy.stats as st
import scipy.integrate as integrate
from sklearn import linear_model

sns.set_style("whitegrid")
sns.set_palette("colorblind")
palette = sns.color_palette()
legend_fontsize = 16

from matplotlib import rc
rc('font',**{'family':'sans-serif'})
rc('text', usetex=True)
rc('text.latex',preamble=r'\usepackage[utf8]{inputenc}')
rc('text.latex',preamble=r'\usepackage[russian]{babel}')
rc('figure', **{'dpi': 300})

figsize = (12,7)
sns_colors = sns.color_palette()

## Байесовский вывод для гауссиана

In [ ]:
def plot_gaussian_with_center(ax, xs, loc, scale, label, color, linewidth=1):
    ax.plot(xs, st.norm.pdf(xs, loc=loc, scale=scale), label=label, color=color, linewidth=linewidth)
    ax.vlines(loc, 0, st.norm.pdf(loc, loc=loc, scale=scale), color=color, linestyle="--", linewidth=linewidth)

In [ ]:
# data = np.random.normal(1, 0.5, 10)
data = np.array([ 1.17454394, -0.18572309, 1.07892128,  0.58878161,  0.83445094,  1.9919644, 0.83162312,  0.97369917,  1.22527845,  1.39177863])

In [ ]:
xmin, xmax, ymax = -2, 3, 1.2
xs = np.arange(xmin, xmax, 0.01)

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)
plot_gaussian_with_center(ax, xs, 1, .5, r"Истинное распределение: $\mathcal{N}(x|\mu=1, \tau=2)$", "black")
ax.scatter(data, np.random.rand(len(data))*0.0, marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, ymax)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
scale = 0.5
xmin, xmax = -5, 5
xs = np.arange(xmin, xmax, 0.01)

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(20):
    ax.plot(xs, st.norm.pdf(xs, loc=np.random.normal(loc=0, scale=1), scale=scale), color="0.3", linewidth=0.5)

ax.plot(xs, st.norm.pdf(xs, loc=np.random.normal(loc=0, scale=1), scale=scale), color="0.3", linewidth=0.5, label=r"Выборка $\mu\sim\mathcal{N}(\mu|\mu_0=0,\tau_0=1)$")
    
ax.scatter(data[:2], np.zeros(2), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, ymax)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
mu_0, tau_0 = 0, 1

In [ ]:
def bayesian_update_mu(mu_0, tau_0, data, tau=2):
    tau_n = tau_0 + len(data)*tau
    mu_n = (tau_0 * mu_0 + tau*np.sum(data)) / tau_n
    return mu_n, tau_n

In [ ]:
mu_n, tau_n = bayesian_update_mu(mu_0, tau_0, data[:2])
print(mu_n, tau_n)

In [ ]:
scale = 0.5
xmin, xmax = -5, 5
xs = np.arange(xmin, xmax, 0.01)

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    plot_gaussian_with_center(ax, xs, np.random.normal(loc=mu_n, scale=np.sqrt(1/tau_n)), scale, None, "0.3", 0.35)

ax.plot(xs, st.norm.pdf(xs, loc=np.random.normal(loc=mu_n, scale=np.sqrt(1/tau_n)), scale=scale), color="0.3", linewidth=0.35, label=r"Выборка $\mu\sim\mathcal{N}(\mu|\mu_2\approx 0.4395,\tau_2=9)$")
    
ax.scatter(data[2:], np.zeros(len(data)-2), marker="*", s=120, label="Новые точки данных")
ax.scatter(data[:2], np.zeros(2), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, ymax)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
mu_m, tau_m = bayesian_update_mu(mu_n, tau_n, data[2:])
print(mu_n, tau_n)
print(mu_m, tau_m)

In [ ]:
scale = 0.5
xmin, xmax = -5, 5
xs = np.arange(xmin, xmax, 0.01)

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    plot_gaussian_with_center(ax, xs, np.random.normal(loc=mu_m, scale=np.sqrt(1/tau_m)), scale, None, "0.3", 0.35)

ax.plot(xs, st.norm.pdf(xs, loc=np.random.normal(loc=mu_m, scale=np.sqrt(1/tau_m)), scale=scale), color="0.3", linewidth=0.35, label=r"Выборка $\mu\sim\mathcal{N}(\mu|\mu_n\approx 0.9664,\tau_n=41)$")
    
ax.scatter(data[:2], np.zeros(2), marker="*", s=120, label="Точки данных")
ax.scatter(data[2:], np.zeros(len(data)-2), marker="*", s=120, label="Новые точки данных")
ax.set_xlim(xmin, xmax)
ax.set_ylim(-0.05, ymax)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
scale = 0.5
xmin, xmax = -5, 5
xs = np.arange(xmin, xmax, 0.01)
alpha_0, beta_0 = 1, 1

fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    ax.plot(xs, st.norm.pdf(xs, loc=1, scale=1/(np.random.gamma(shape=alpha_0, scale=1/beta_0))), color="0.3", linewidth=0.5)

ax.plot(xs, st.norm.pdf(xs, loc=1, scale=1/(np.random.gamma(shape=alpha_0, scale=1/beta_0))), color="0.3", linewidth=0.5, label=r"Выборка $\tau\sim\mathrm{Gamma}(\tau|\alpha_0= %d,\beta_0=%d)$" % (alpha_0, beta_0))
ax.vlines(1, -1, 1.5, linewidth=.5, color="0.3", linestyle="--")
    
ax.scatter(data[:2], np.zeros(2), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, ymax)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
def bayesian_update_tau(alpha_0, beta_0, data, mu=1):
    alpha_n = alpha_0 + len(data)*0.5
    beta_n = beta_0 + 0.5 * np.sum((data-mu)**2)
    return alpha_n, beta_n

In [ ]:
alpha_2, beta_2 = bayesian_update_tau(alpha_0, beta_0, data)

In [ ]:
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    ax.plot(xs, st.norm.pdf(xs, loc=1, scale=1/(np.random.gamma(shape=alpha_2, scale=1./beta_2))), color="0.3", linewidth=0.5)

ax.plot(xs, st.norm.pdf(xs, loc=1, scale=1/(np.random.gamma(shape=alpha_2, scale=1./beta_2))), color="0.3", linewidth=0.5, label=r"Выборка $\tau\sim\mathrm{Gamma}(\tau|\alpha_n= %d,\beta_n\approx %.3f)$" % (alpha_2, beta_2))
ax.vlines(1, -1, 1.5, linewidth=.5, color="0.3", linestyle="--")
    
ax.scatter(data, np.zeros(len(data)), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, ymax)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
data2 = np.random.normal(1, 1, 20)
alpha_a, beta_a = bayesian_update_tau(alpha_0, beta_0, data2, mu=-1)
alpha_b, beta_b = bayesian_update_tau(alpha_0, beta_0, data2, mu=1)

In [ ]:
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    ax.plot(xs, st.norm.pdf(xs, loc=-1, scale=1/(np.random.gamma(shape=alpha_a, scale=1./beta_a))), color="0.3", linewidth=0.5)

ax.plot(xs, st.norm.pdf(xs, loc=-1, scale=1/(np.random.gamma(shape=alpha_a, scale=1./beta_a))), color="0.3", linewidth=0.5, label=r"Выборка $\tau\sim\mathrm{Gamma}(\tau|\alpha_n= %d,\beta_n\approx %.3f)$" % (alpha_a, beta_a))
ax.vlines(-1, -1, .5, linewidth=.5, color="0.3", linestyle="--")

ax.scatter(data2, np.zeros(len(data2)), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.02, .5)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    ax.plot(xs, st.norm.pdf(xs, loc=1, scale=1/(np.random.gamma(shape=alpha_b, scale=1./beta_b))), color="0.3", linewidth=0.5)

ax.plot(xs, st.norm.pdf(xs, loc=1, scale=1/(np.random.gamma(shape=alpha_b, scale=1./beta_b))), color="0.3", linewidth=0.5, label=r"Выборка $\tau\sim\mathrm{Gamma}(\tau|\alpha_n= %d,\beta_n\approx %.3f)$" % (alpha_b, beta_b))
ax.vlines(1, -1, .5, linewidth=.5, color="0.3", linestyle="--")

ax.scatter(data2, np.zeros(len(data2)), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, 1.5)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
def p_mt(mu, tau, alpha, beta, mu_mu, lmb):
    return st.gamma.pdf(tau, alpha, scale = 1./beta) * st.norm.pdf(mu, loc=mu_mu, scale = 1./(lmb*tau))

def p_prior(mu, tau):
    return p_mt(mu, tau, 1., 1., 0, 1.)

In [ ]:
zs_mu, zs_tau = np.arange(-3, 3, 0.025), np.arange(0.0001, 3, 0.025)
Z = np.array([[ p_prior(mu, tau) for mu in zs_mu] for tau in zs_tau])

In [ ]:
fig = plt.figure(figsize=(figsize[0]/1.5, figsize[1]/1.5))
ax = fig.add_subplot(111)
ax.set_xlim((-3, 3))
ax.set_ylim((0.02, 3))

heatmap = plt.pcolormesh(zs_mu, zs_tau, Z, cmap=plt.cm.jet)
plt.colorbar(heatmap, fraction=0.1)

In [ ]:
def bayesian_update_mt(alpha, beta, mu, lmb, data):
    n = len(data)
    lmb_n = lmb + n
    mu_n = (lmb*mu + np.sum(data)) / lmb_n
    alpha_n = alpha + n / 2.
    beta_n = beta + lmb*mu*mu + np.sum(data ** 2) - (mu_n**2)*lmb_n
    return alpha_n, beta_n, mu_n, lmb_n

In [ ]:
a, b, m, l = bayesian_update_mt(1., 1., 0., 1., data[:5])

In [ ]:
Z = np.array([[ p_mt(mu, tau, a, b, m, l) for mu in zs_mu] for tau in zs_tau])

In [ ]:
fig = plt.figure(figsize=(figsize[0]/1.5, figsize[1]/1.5))
ax = fig.add_subplot(111)
ax.set_xlim((-3, 3))
ax.set_ylim((0.02, 3))

heatmap = plt.pcolormesh(zs_mu, zs_tau, Z, cmap=plt.cm.jet)
plt.colorbar(heatmap, fraction=0.1)

In [ ]:
def sample_mt(alpha, beta, mu, lmb):
    tau = np.random.gamma(shape=alpha, scale=1./beta)
    m = np.random.normal(loc=mu, scale=1./(lmb*tau))
    return m, tau

In [ ]:
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    mu, t = sample_mt(1, 1, 0, 1)
    ax.plot(xs, st.norm.pdf(xs, loc=mu, scale=1/(t)), color="0.3", linewidth=0.5)

mu, t = sample_mt(1, 1, 0, 1)
ax.plot(xs, st.norm.pdf(xs, loc=mu, scale=1/t), color="0.3", linewidth=0.5, label=r"Выборка $\mu,\tau\sim p(\mu,\tau)$")
ax.vlines(1, -1, .5, linewidth=.5, color="0.3", linestyle="--")

ax.scatter(data[:5], np.zeros(len(data[:5])), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, 1.5)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

for _ in range(10):
    mu, t = sample_mt(a, b, m, l)
    ax.plot(xs, st.norm.pdf(xs, loc=mu, scale=1/(t)), color="0.3", linewidth=0.5)

mu, t = sample_mt(a, b, m, l)
ax.plot(xs, st.norm.pdf(xs, loc=mu, scale=1/t), color="0.3", linewidth=0.5, label=r"Выборка $\mu,\tau\sim p(\mu,\tau|D)$")
ax.vlines(1, -1, .5, linewidth=.5, color="0.3", linestyle="--")

ax.scatter(data[:5], np.zeros(len(data[:5])), marker="*", s=120, label="Точки данных")
ax.set_xlim(xmin,xmax)
ax.set_ylim(-0.05, 1.5)
ax.set_xticks(np.arange(xmin, xmax+1, 1))
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
print(a,b,m,l)

In [ ]:
mus = np.array([ sample_mt(a, b, m, l)[0] for _ in range(100000) ])

In [ ]:
theta = st.t.fit(mus)

In [ ]:
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

ax.hist(mus, bins=200, linewidth=0.1, density=True, color="0.7")

xs = np.arange(-7, 5, 0.01)
ax.plot(xs, st.norm.pdf(xs, loc=np.mean(mus), scale=np.std(mus)), color=sns_colors[0], linewidth=1.5, label="Нормальное распределение")
ax.plot(xs, st.t.pdf(xs, df=theta[0], loc=theta[1], scale=theta[2]), color=sns_colors[2], linewidth=1.5, label="Распределение Стьюдента")
ax.legend(loc="upper left", fontsize=legend_fontsize-2)

In [ ]:
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

ax.hist(mus, bins=200, linewidth=0.1, density=True, color="0.7")

xs = np.arange(-7, 5, 0.01)
ax.plot(xs, st.norm.pdf(xs, loc=np.mean(mus), scale=np.std(mus)), color=sns_colors[0], linewidth=1.5, label="Нормальное распределение")
ax.plot(xs, st.t.pdf(xs, df=theta[0], loc=theta[1], scale=theta[2]), color=sns_colors[2], linewidth=1.5, label="Распределение Стьюдента")
ax.legend(loc="upper left", fontsize=legend_fontsize-2)
ax.set_ylim(0.0, 0.005)

In [ ]:
mts = np.array([ sample_mt(a, b, m, l) for _ in range(100000) ])
new_xs = np.array([ np.random.normal(loc=params[0], scale=1./params[1]) for params in mts ])

In [ ]:
theta = st.t.fit(new_xs)

In [ ]:
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

ax.hist(new_xs, bins=500, linewidth=0.1, density=True, color="0.7")

xs = np.arange(-20, 20, 0.1)
ax.plot(xs, st.norm.pdf(xs, loc=np.mean(new_xs), scale=np.std(new_xs)), color=sns_colors[0], linewidth=1.5, label="Нормальное распределение")
ax.plot(xs, st.t.pdf(xs, df=theta[0], loc=theta[1], scale=theta[2]), color=sns_colors[2], linewidth=1.5, label="Распределение Стьюдента")
ax.legend(loc="upper left", fontsize=legend_fontsize-2)
ax.set_xlim(-20, 20)

In [ ]:
fig = plt.figure(figsize=(figsize[0]/2, figsize[1]/1.5))
ax = fig.add_subplot(111)

ax.hist(new_xs, bins=500, linewidth=0.1, density=True, color="0.7")

xs = np.arange(-40, 40, 0.1)
ax.plot(xs, st.norm.pdf(xs, loc=np.mean(new_xs), scale=np.std(new_xs)), color=sns_colors[0], linewidth=1.5, label="Нормальное распределение")
ax.plot(xs, st.t.pdf(xs, df=theta[0], loc=theta[1], scale=theta[2]), color=sns_colors[2], linewidth=1.5, label="Распределение Стьюдента")
ax.legend(loc="upper left", fontsize=legend_fontsize-2)
ax.set_xlim(-20, 20)
ax.set_ylim(0.0, 0.025)